In [3]:
import torch

USE_GPU = True
device = 0
if USE_GPU and torch.cuda.is_available():
    device = torch.device('cuda')
else:
    device = torch.device('cpu')
print('using device:', device)
dtype = torch.float32 # we will be using float throughout this tutorial
# Constant to control how frequently we print train loss
print_every = 100

using device: cuda


In [4]:
import MPII
import convnet
from torch.utils import data as D

root = 'D:\_github\experiments\\filitzin\\1_max90'
csv_path = 'D:\_github\experiments\\filitzin\\filitzin.csv'
"""
master_dataset = MPII.MPII(root, csv_path)
n = len(master_dataset)
test_n = int(0.1*n)
train_n = n - test_n
train_dataset, test_dataset = D.random_split(master_dataset, (train_n, test_n))
train_dataloader = D.DataLoader(train_dataset, batch_size = 15)
test_dataloader = D.DataLoader(test_dataset, batch_size = 15)
"""
train_dataset = MPII.MPII(root, csv_path)
train_dataloader = D.DataLoader(train_dataset, batch_size = 15)
val_dataloader = D.DataLoader(train_dataset, batch_size = 15)

In [10]:
print(len(train_dataset))
width = 600
height = 480
chanels = 3

im_size = (width, height, chanels)

num_filters = 9 # depth
conv_kernel = 3 # 3*3
pooling_kernel = 2 #2*2

conv_tuple =  (num_filters, conv_kernel, pooling_kernel)
conv_params = [conv_tuple, conv_tuple, conv_tuple]

linear1 = 10
linear2 = 5 # число классов

linear_params = [linear1, linear2]

model = convnet.ConvNet(im_size, conv_params, linear_params)

377


In [11]:
import torch.optim as optim

learning_rate = 1e-2
optimizer = optim.SGD(model.parameters(), lr=learning_rate,
                     momentum=0.9, nesterov=True)
epochs = 25

In [12]:
def check_accuracy_part34(loader, model, file_path):
    #if loader.dataset.train:
        #print('Checking accuracy on validation set')
    #else:
        #print('Checking accuracy on test set')   
    num_correct = 0
    num_samples = 0
    model.eval()  # set model to evaluation mode
    with torch.no_grad():
        for x, y in loader:
            x = x.to(device=device, dtype=dtype)  # move to device, e.g. GPU
            y = y.to(device=device, dtype=torch.long)
            scores = model(x)
            _, preds = scores.max(1)
            num_correct += (preds == y).sum()
            num_samples += preds.size(0)
        acc = float(num_correct) / num_samples
        with open(file_path, "a") as file:
            print('Got %d / %d correct (%.2f)\n\n' % (num_correct, num_samples, 100 * acc), file=file)

In [13]:
import torch.nn.functional as F

def train_part34(model, optimizer, device, epochs, file_path):
    """
    Train a model on CIFAR-10 using the PyTorch Module API.
    
    Inputs:
    - model: A PyTorch Module giving the model to train.
    - optimizer: An Optimizer object we will use to train the model
    - epochs: (Optional) A Python integer giving the number of epochs to train for
    
    Returns: Nothing, but prints model accuracies during training.
    """
    #loader_train = train_dataloader
    
    model = model.to(device=device)  # move the model parameters to CPU/GPU
    for e in range(epochs):
        for t, (x, y) in enumerate(train_dataloader):
            model.train()  # put model to training mode
            x = x.to(device=device, dtype=dtype)  # move to device, e.g. GPU
            print(x)
            y = y.to(device=device, dtype=torch.long)

            scores = model(x)
            loss = F.cross_entropy(scores, y)

            # Zero out all of the gradients for the variables which the optimizer
            # will update.
            optimizer.zero_grad()

            # This is the backwards pass: compute the gradient of the loss with
            # respect to each  parameter of the model.
            loss.backward()

            # Actually update the parameters of the model using the gradients
            # computed by the backwards pass.
            optimizer.step()

            if t % print_every == 0:
                with open(file_path, "a") as file:
                    print('Iteration %d, loss = %.4f\n' % (t, loss.item()), file=file)
                check_accuracy_part34(val_dataloader, model, file_path) # check_accuracy_part34(test_dataloader, model, file_path)
                #print()

In [14]:
import csv
print("FIRST EXPERIMENT")
train_part34(model, optimizer, device, epochs, 'D:\_github\experiments\\filitzin\\25e_max90.txt')
print("END EXPERIMENTS")

PATH = 'D:\_github\experiments\\filitzin\\filitzin_model.pth'
torch.save(model.state_dict(), PATH)

"""
model.eval()

csv_labels =[]
csv_predicted =[]

with torch.no_grad():
    for data in test_dataloader:
        images, labels = data
        images = images.to(device = device, dtype = dtype)
        labels = labels.to(device = device, dtype = torch.long)
        outputs = model(images)
        _, predicted = torch.max(outputs, 1)        
        for label in labels:
            csv_labels.append(label.item())
        for pred in predicted:
            csv_predicted.append(pred.item())

rows_to_csv =[]
for i in range(len(csv_labels)):
    rows_to_csv.append([i, csv_labels[i], csv_predicted[i]])
    if(csv_labels[i]!=csv_predicted[i]):
        print(i)
        
path = 'D:\_github\experiments\experient_3\\3_test.csv'
with open(path, "w", newline='') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    for line in rows_to_csv:
        writer.writerow(line)
        

        
csv_labels =[]
csv_predicted =[]

with torch.no_grad():
    for data in train_dataloader:
        images, labels = data
        images = images.to(device = device, dtype = dtype)
        labels = labels.to(device = device, dtype = torch.long)
        outputs = model(images)
        _, predicted = torch.max(outputs, 1)        
        for label in labels:
            csv_labels.append(label.item())
        for pred in predicted:
            csv_predicted.append(pred.item())

rows_to_csv =[]
for i in range(len(csv_labels)):
    rows_to_csv.append([i, csv_labels[i], csv_predicted[i]])
    if(csv_labels[i]!=csv_predicted[i]):
        print(i)
        
path = 'D:\_github\experiments\experient_3\\3_train.csv'
with open(path, "w", newline='') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    for line in rows_to_csv:
        writer.writerow(line)
"""

FIRST EXPERIMENT
tensor([[[[0.0745, 0.0784, 0.0627,  ..., 0.1647, 0.2627, 0.2118],
          [0.0784, 0.0824, 0.0627,  ..., 0.1686, 0.2510, 0.2039],
          [0.0745, 0.0824, 0.0627,  ..., 0.1490, 0.2118, 0.1725],
          ...,
          [0.1922, 0.1922, 0.1922,  ..., 0.1373, 0.1373, 0.1373],
          [0.1922, 0.1922, 0.1922,  ..., 0.1373, 0.1333, 0.1333],
          [0.1843, 0.1922, 0.1922,  ..., 0.1333, 0.1333, 0.1294]],

         [[0.0902, 0.0941, 0.0784,  ..., 0.1647, 0.2627, 0.2118],
          [0.0941, 0.0980, 0.0784,  ..., 0.1686, 0.2510, 0.2039],
          [0.0902, 0.0980, 0.0784,  ..., 0.1490, 0.2118, 0.1725],
          ...,
          [0.0784, 0.0784, 0.0784,  ..., 0.0549, 0.0549, 0.0549],
          [0.0784, 0.0784, 0.0784,  ..., 0.0549, 0.0510, 0.0510],
          [0.0824, 0.0784, 0.0784,  ..., 0.0510, 0.0510, 0.0471]],

         [[0.1373, 0.1412, 0.1255,  ..., 0.3137, 0.4118, 0.3608],
          [0.1412, 0.1451, 0.1255,  ..., 0.3176, 0.4000, 0.3529],
          [0.1373, 0.1451

tensor([[[[0.3098, 0.5569, 0.5686,  ..., 0.5451, 0.5294, 0.2706],
          [0.5294, 0.7882, 0.8157,  ..., 0.7961, 0.7647, 0.4980],
          [0.4941, 0.7686, 0.8157,  ..., 0.7922, 0.7451, 0.4706],
          ...,
          [0.1294, 0.3725, 0.4078,  ..., 0.7294, 0.6941, 0.4784],
          [0.1765, 0.4549, 0.3804,  ..., 0.7176, 0.6863, 0.4706],
          [0.1059, 0.2549, 0.1294,  ..., 0.5373, 0.5059, 0.2902]],

         [[0.3922, 0.6392, 0.6510,  ..., 0.6471, 0.6235, 0.3647],
          [0.6118, 0.8706, 0.8980,  ..., 0.8980, 0.8588, 0.5922],
          [0.5765, 0.8510, 0.8980,  ..., 0.8941, 0.8392, 0.5647],
          ...,
          [0.2471, 0.4902, 0.5373,  ..., 0.6941, 0.6588, 0.4431],
          [0.2941, 0.5725, 0.4980,  ..., 0.6824, 0.6510, 0.4353],
          [0.2235, 0.3725, 0.2471,  ..., 0.5020, 0.4706, 0.2549]],

         [[0.4745, 0.7216, 0.7333,  ..., 0.7451, 0.7255, 0.4588],
          [0.6941, 0.9529, 0.9804,  ..., 0.9961, 0.9608, 0.6863],
          [0.6588, 0.9333, 0.9804,  ..., 0

tensor([[[[0.2824, 0.5804, 0.5412,  ..., 0.0000, 0.0039, 0.0196],
          [0.2824, 0.5804, 0.5412,  ..., 0.0000, 0.0039, 0.0196],
          [0.2824, 0.5804, 0.5412,  ..., 0.0000, 0.0039, 0.0196],
          ...,
          [0.5569, 0.8588, 0.7529,  ..., 0.0039, 0.0078, 0.0000],
          [0.5647, 0.8157, 0.7451,  ..., 0.0039, 0.0078, 0.0039],
          [0.5373, 0.7647, 0.7294,  ..., 0.0039, 0.0078, 0.0039]],

         [[0.5451, 0.8431, 0.8039,  ..., 0.0196, 0.0000, 0.0000],
          [0.5451, 0.8431, 0.8039,  ..., 0.0196, 0.0000, 0.0000],
          [0.5451, 0.8431, 0.8039,  ..., 0.0196, 0.0000, 0.0000],
          ...,
          [0.5333, 0.8353, 0.7294,  ..., 0.0000, 0.0078, 0.0000],
          [0.5412, 0.7922, 0.7216,  ..., 0.0000, 0.0078, 0.0039],
          [0.5137, 0.7412, 0.7059,  ..., 0.0000, 0.0078, 0.0039]],

         [[0.7137, 1.0000, 0.9725,  ..., 0.0431, 0.0000, 0.0000],
          [0.7137, 1.0000, 0.9725,  ..., 0.0431, 0.0000, 0.0000],
          [0.7137, 1.0000, 0.9725,  ..., 0

tensor([[[[0.6235, 0.5843, 0.4941,  ..., 0.5059, 0.4392, 0.3412],
          [0.6275, 0.5059, 0.4392,  ..., 0.4235, 0.4275, 0.3922],
          [0.6196, 0.5490, 0.5216,  ..., 0.3451, 0.4157, 0.3725],
          ...,
          [0.2627, 0.2824, 0.3137,  ..., 0.3137, 0.2863, 0.2745],
          [0.2667, 0.2784, 0.3137,  ..., 0.3333, 0.3176, 0.3098],
          [0.2667, 0.2745, 0.3137,  ..., 0.3412, 0.3294, 0.3255]],

         [[0.5686, 0.5294, 0.4392,  ..., 0.5059, 0.4471, 0.3490],
          [0.5647, 0.4549, 0.3882,  ..., 0.4235, 0.4353, 0.4000],
          [0.5569, 0.4863, 0.4706,  ..., 0.3529, 0.4235, 0.3804],
          ...,
          [0.3882, 0.4078, 0.4392,  ..., 0.4471, 0.4196, 0.4078],
          [0.3922, 0.4039, 0.4392,  ..., 0.4667, 0.4549, 0.4471],
          [0.3922, 0.4000, 0.4392,  ..., 0.4784, 0.4667, 0.4627]],

         [[0.2745, 0.2353, 0.1451,  ..., 0.2627, 0.1922, 0.0902],
          [0.2627, 0.1490, 0.0824,  ..., 0.1725, 0.1804, 0.1412],
          [0.2510, 0.1804, 0.1608,  ..., 0

tensor([[[[0.1294, 0.1490, 0.1765,  ..., 0.1216, 0.1451, 0.1412],
          [0.1333, 0.1490, 0.1725,  ..., 0.1373, 0.1608, 0.1569],
          [0.1412, 0.1529, 0.1647,  ..., 0.2392, 0.2667, 0.2706],
          ...,
          [0.4000, 0.3961, 0.3922,  ..., 0.1098, 0.1098, 0.1098],
          [0.4039, 0.3961, 0.3882,  ..., 0.1098, 0.1098, 0.1137],
          [0.4000, 0.3922, 0.3843,  ..., 0.1098, 0.1098, 0.1137]],

         [[0.1255, 0.1451, 0.1765,  ..., 0.0706, 0.0863, 0.0745],
          [0.1294, 0.1451, 0.1725,  ..., 0.0784, 0.0941, 0.0902],
          [0.1373, 0.1490, 0.1647,  ..., 0.1725, 0.1922, 0.1961],
          ...,
          [0.4000, 0.3961, 0.3922,  ..., 0.1098, 0.1098, 0.1098],
          [0.4039, 0.3961, 0.3882,  ..., 0.1098, 0.1098, 0.1137],
          [0.4000, 0.3922, 0.3843,  ..., 0.1098, 0.1098, 0.1137]],

         [[0.1451, 0.1647, 0.1843,  ..., 0.0980, 0.1137, 0.0980],
          [0.1490, 0.1647, 0.1804,  ..., 0.1059, 0.1176, 0.1137],
          [0.1569, 0.1686, 0.1725,  ..., 0

...

tensor([[[[0.6353, 0.6392, 0.6431,  ..., 0.5333, 0.5059, 0.5020],
          [0.6353, 0.6392, 0.6431,  ..., 0.5373, 0.5176, 0.5020],
          [0.6353, 0.6392, 0.6431,  ..., 0.5373, 0.5216, 0.5059],
          ...,
          [0.6588, 0.6588, 0.6549,  ..., 0.6471, 0.6549, 0.6588],
          [0.6588, 0.6588, 0.6588,  ..., 0.6706, 0.6745, 0.6745],
          [0.6588, 0.6588, 0.6627,  ..., 0.6863, 0.6863, 0.6863]],

         [[0.4667, 0.4706, 0.4745,  ..., 0.5098, 0.4824, 0.4667],
          [0.4667, 0.4706, 0.4745,  ..., 0.5137, 0.4824, 0.4667],
          [0.4667, 0.4706, 0.4745,  ..., 0.5137, 0.4863, 0.4745],
          ...,
          [0.4275, 0.4275, 0.4235,  ..., 0.4353, 0.4431, 0.4471],
          [0.4275, 0.4275, 0.4275,  ..., 0.4588, 0.4627, 0.4627],
          [0.4275, 0.4275, 0.4314,  ..., 0.4745, 0.4745, 0.4745]],

         [[0.2902, 0.2941, 0.2980,  ..., 0.3843, 0.3490, 0.3373],
          [0.2902, 0.2941, 0.2980,  ..., 0.3882, 0.3529, 0.3373],
          [0.2902, 0.2941, 0.2980,  ..., 0

tensor([[[[0.0980, 0.0902, 0.0667,  ..., 0.0118, 0.0353, 0.0941],
          [0.0824, 0.0824, 0.0667,  ..., 0.0039, 0.0275, 0.0863],
          [0.0549, 0.0549, 0.0471,  ..., 0.0078, 0.0196, 0.0706],
          ...,
          [0.6667, 0.6667, 0.6706,  ..., 0.8510, 0.9020, 0.9137],
          [0.6784, 0.6824, 0.6824,  ..., 0.8314, 0.8510, 0.8510],
          [0.6941, 0.6941, 0.6902,  ..., 0.8118, 0.8118, 0.8000]],

         [[0.0667, 0.0588, 0.0353,  ..., 0.0078, 0.0314, 0.0902],
          [0.0510, 0.0510, 0.0353,  ..., 0.0000, 0.0235, 0.0824],
          [0.0196, 0.0196, 0.0118,  ..., 0.0039, 0.0157, 0.0667],
          ...,
          [0.5412, 0.5412, 0.5451,  ..., 0.7137, 0.7647, 0.7804],
          [0.5529, 0.5569, 0.5569,  ..., 0.6941, 0.7216, 0.7176],
          [0.5686, 0.5686, 0.5647,  ..., 0.6745, 0.6824, 0.6667]],

         [[0.0549, 0.0471, 0.0275,  ..., 0.0000, 0.0157, 0.0745],
          [0.0392, 0.0392, 0.0235,  ..., 0.0000, 0.0078, 0.0667],
          [0.0000, 0.0000, 0.0000,  ..., 0

tensor([[[[0.5176, 0.5765, 0.5373,  ..., 0.2706, 0.3098, 0.3490],
          [0.5098, 0.5569, 0.5294,  ..., 0.2706, 0.3137, 0.3529],
          [0.5176, 0.5451, 0.5333,  ..., 0.2706, 0.3176, 0.3569],
          ...,
          [0.5647, 0.5608, 0.5569,  ..., 0.2510, 0.3216, 0.5059],
          [0.5529, 0.5490, 0.5490,  ..., 0.2510, 0.2980, 0.5176],
          [0.5725, 0.5608, 0.5529,  ..., 0.2471, 0.2863, 0.5333]],

         [[0.5569, 0.6157, 0.5765,  ..., 0.3059, 0.3451, 0.3843],
          [0.5490, 0.5961, 0.5686,  ..., 0.3059, 0.3490, 0.3882],
          [0.5569, 0.5843, 0.5725,  ..., 0.3059, 0.3529, 0.3922],
          ...,
          [0.6118, 0.6078, 0.6039,  ..., 0.2706, 0.3412, 0.5373],
          [0.6000, 0.5961, 0.5961,  ..., 0.2627, 0.3176, 0.5490],
          [0.6196, 0.6078, 0.6000,  ..., 0.2588, 0.3059, 0.5529]],

         [[0.5922, 0.6510, 0.6118,  ..., 0.2941, 0.3412, 0.3804],
          [0.5843, 0.6314, 0.6039,  ..., 0.2941, 0.3451, 0.3843],
          [0.5922, 0.6196, 0.6078,  ..., 0

tensor([[[[0.1569, 0.2902, 0.3529,  ..., 0.3373, 0.3020, 0.1922],
          [0.2588, 0.4392, 0.5294,  ..., 0.5176, 0.4588, 0.3098],
          [0.2510, 0.4706, 0.5686,  ..., 0.5529, 0.4549, 0.2667],
          ...,
          [0.3216, 0.4275, 0.4392,  ..., 0.8863, 0.8431, 0.5569],
          [0.2980, 0.3882, 0.4039,  ..., 0.8784, 0.8353, 0.5765],
          [0.1412, 0.2275, 0.2627,  ..., 0.6275, 0.6039, 0.3686]],

         [[0.1922, 0.3255, 0.3882,  ..., 0.3686, 0.3412, 0.2392],
          [0.2941, 0.4745, 0.5647,  ..., 0.5608, 0.4980, 0.3608],
          [0.2902, 0.5098, 0.6078,  ..., 0.6000, 0.4980, 0.3216],
          ...,
          [0.4196, 0.5255, 0.5373,  ..., 0.9020, 0.8588, 0.5725],
          [0.3961, 0.4863, 0.5020,  ..., 0.8941, 0.8510, 0.5922],
          [0.2392, 0.3255, 0.3608,  ..., 0.6431, 0.6196, 0.3843]],

         [[0.0784, 0.2118, 0.2745,  ..., 0.2745, 0.2471, 0.1529],
          [0.1804, 0.3608, 0.4510,  ..., 0.4431, 0.3922, 0.2588],
          [0.1843, 0.4039, 0.5020,  ..., 0

'\nmodel.eval()\n\ncsv_labels =[]\ncsv_predicted =[]\n\nwith torch.no_grad():\n    for data in test_dataloader:\n        images, labels = data\n        images = images.to(device = device, dtype = dtype)\n        labels = labels.to(device = device, dtype = torch.long)\n        outputs = model(images)\n        _, predicted = torch.max(outputs, 1)        \n        for label in labels:\n            csv_labels.append(label.item())\n        for pred in predicted:\n            csv_predicted.append(pred.item())\n\nrows_to_csv =[]\nfor i in range(len(csv_labels)):\n    rows_to_csv.append([i, csv_labels[i], csv_predicted[i]])\n    if(csv_labels[i]!=csv_predicted[i]):\n        print(i)\n        \npath = \'D:\\_github\\experiments\\experient_3\\3_test.csv\'\nwith open(path, "w", newline=\'\') as csv_file:\n    writer = csv.writer(csv_file, delimiter=\',\')\n    for line in rows_to_csv:\n        writer.writerow(line)\n        \n\n        \ncsv_labels =[]\ncsv_predicted =[]\n\nwith torch.no_grad():\

In [8]:
PATH = 'D:\_github\experiments\experient_3\\3_model.pth'
torch.save(model.state_dict(), PATH)

In [13]:
model.eval()

ConvNet(
  (layers): ModuleList(
    (0): ConvUnit(
      (nn): Sequential(
        (0): Conv2d(3, 9, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (1): BatchNorm2d(9, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): LeakyReLU(negative_slope=0.01)
        (3): Conv2d(9, 9, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (4): BatchNorm2d(9, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (5): LeakyReLU(negative_slope=0.01)
        (6): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
      )
    )
    (1): ConvUnit(
      (nn): Sequential(
        (0): Conv2d(9, 9, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (1): BatchNorm2d(9, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (2): LeakyReLU(negative_slope=0.01)
        (3): Conv2d(9, 9, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (4): BatchNorm2d(9, eps=1e-05, momentum=0.1, affine=Tru

In [14]:
csv_labels =[]
csv_predicted =[]

with torch.no_grad():
    for data in test_dataloader:
        images, labels = data
        images = images.to(device = device, dtype = dtype)
        labels = labels.to(device = device, dtype = torch.long)
        outputs = model(images)
        _, predicted = torch.max(outputs, 1)        
        for label in labels:
            csv_labels.append(label.item())
        for pred in predicted:
            csv_predicted.append(pred.item())
            
print(csv_labels[0])
print(csv_predicted[0])

4
4


In [15]:
rows_to_csv =[]
for i in range(len(csv_labels)):
    rows_to_csv.append([i, csv_labels[i], csv_predicted[i]])
    if(csv_labels[i]!=csv_predicted[i]):
        print(i)    
print(len(rows_to_csv))

1
9
12
13
14
25
40
48
55
59
63
72
75
76
82
83
86
90
94
98
105
111
114
123
128
133
134
155
161
167
170
172
175
179
199
206
210
212
217
230
237
241
243
246
247
248
249
252
253
256
262
265
271
276
281
284
292


In [16]:
import csv
path = 'D:\_github\experiments\experient_3\\2_test.csv'
with open(path, "w", newline='') as csv_file:
    writer = csv.writer(csv_file, delimiter=',')
    for line in rows_to_csv:
        writer.writerow(line)

True
